In [1]:
#!gsutil -m cp gs://terra-featured-workspaces/Sc_SnRNA-seq/data/mouse_cortex/raw_feature_bc_matrix.h5 ./mouse/
#!gsutil -m cp gs://terra-featured-workspaces/Sc_SnRNA-seq/data/mouse_cortex_ADT/mouse_cortex_ADT.csv ./mouse/

In [2]:
#!sccloud demuxEM -p 8 --min-num-genes 200 --generate-diagnostic-plots ./mouse/mouse_cortex_ADT.csv ./mouse/raw_feature_bc_matrix.h5 ./mouse/exp

In [3]:
import sccloud as scc
import numpy as np

//anaconda3/envs/sccloud/lib/python3.7/site-packages/lightgbm/__init__.py:46: UserWarning: Starting from version 2.2.1, the library file in distribution wheels for macOS is built by the Apple Clang (Xcode_9.4.1) compiler.
This means that in case of installing LightGBM from PyPI via the ``pip install lightgbm`` command, you don't need to install the gcc compiler anymore.
Instead of that, you need to install the OpenMP library, which is required for running LightGBM on the system with the Apple Clang compiler.
You can install the OpenMP library by the following command: ``brew install libomp``.
  "You can install the OpenMP library by the following command: ``brew install libomp``.", UserWarning)


## Preprocessing

In [4]:
adata = scc.read_input("./mouse/exp_demux.h5sc", select_singlets = True)
adata

2019-08-23 12:01:09,768 - sccloud - INFO - Read input is finished. Time spent = 1.05s.


AnnData object with n_obs × n_vars = 3267 × 27998 
    obs: 'assignment', 'Channel'
    var: 'gene_ids'
    uns: 'genome'

In [5]:
adata.obs['assignment'].value_counts()

Sample5M    502
Sample8M    467
Sample6M    408
Sample2F    397
Sample1F    397
Sample3F    376
Sample7M    367
Sample4F    353
Name: assignment, dtype: int64

In [6]:
scc.qc_metrics(adata, mito_prefix = 'mt-', min_genes = 200)

In [7]:
adata.var.keys()

Index(['gene_ids', 'n_cells', 'percent_cells', 'robust',
       'highly_variable_features'],
      dtype='object')

In [8]:
adata.obs.keys()

Index(['assignment', 'Channel', 'passed_qc', 'n_genes', 'n_counts',
       'percent_mito'],
      dtype='object')

In [9]:
scc.violin(adata, keys = ['n_genes', 'n_counts', 'percent_mito'], by = 'passed_qc')

:Layout
   .Violin.I   :Violin   [passed_qc]   (n_genes)
   .Violin.II  :Violin   [passed_qc]   (n_counts)
   .Violin.III :Violin   [passed_qc]   (percent_mito)

In [10]:
scc.scatter_matrix(adata, ['n_genes', 'n_counts', 'percent_mito'], color='passed_qc')

:GridMatrix   [X,Y]
   :NdOverlay   [passed_qc]
      :Histogram   [percent_mito]   (percent_mito_frequency)

In [11]:
scc.violin(adata, keys = ['n_cells'])

:Layout
   .Violin.I :Violin   (n_cells)

In [12]:
scc.filter_data(adata)
adata

2019-08-23 12:01:11,599 - sccloud - INFO - After filteration, 3219 cells and 20353 genes are kept. Among 20353 genes, 18870 genes are robust.


AnnData object with n_obs × n_vars = 3219 × 20353 
    obs: 'assignment', 'Channel', 'passed_qc', 'n_genes', 'n_counts', 'percent_mito'
    var: 'gene_ids', 'n_cells', 'percent_cells', 'robust', 'highly_variable_features'
    uns: 'genome'

In [13]:
scc.log_norm(adata, norm_count = 1e5)

2019-08-23 12:01:11,746 - sccloud - INFO - Normalization is finished. Time spent = 0.14s.


In [14]:
scc.highly_variable_features(adata, consider_batch = False)

2019-08-23 12:01:11,882 - sccloud - INFO - 2000 highly variable features have been selected. Time spent = 0.13s.


In [15]:
scc.variable_feature_plot(adata)

:Overlay
   .NdOverlay.I :NdOverlay   [highly_variable_features]
      :Scatter   [mean]   (var,id)
   .Curve.I     :Curve   [mean]   (hvf_loess,id)

In [16]:
scc.pca(adata)

2019-08-23 12:01:12,457 - sccloud - INFO - PCA is done. Time spent = 0.18s.


In [17]:
scc.neighbors(adata)

2019-08-23 12:01:12,811 - sccloud - INFO - Nearest neighbor search is finished in 0.35s.
2019-08-23 12:01:12,897 - sccloud - INFO - Constructing affinity matrix is done. Time spent = 0.09s.
2019-08-23 12:01:12,898 - sccloud - INFO - Affinity matrix calculation is finished in 0.09s


## Clustering

In [18]:
scc.leiden(adata, n_iter = 2)

2019-08-23 12:01:13,019 - sccloud - INFO - Graph is constructed. Time spent = 0.12s.
2019-08-23 12:01:13,343 - sccloud - INFO - Leiden clustering is done. Time spent = 0.44s.


In [19]:
scc.composition_plot(adata, by = 'leiden_labels', condition = 'assignment')

:Layout
   .Bars.I  :Bars   [leiden_labels,assignment]   (value)
   .Table.I :Table   [cluster,fdr,bonferroni,p_value,chi2]

## Dimension Reduction

In [20]:
scc.fitsne(adata)

2019-08-23 12:01:41,076 - sccloud - INFO - FIt-SNE is calculated. Time spent = 27.57s.


In [21]:
scc.embedding(adata, basis = 'fitsne', keys = ['leiden_labels', 'assignment'])

:Layout
   .NdOverlay.I  :NdOverlay   [leiden_labels]
      :Scatter   [X_fitsne1]   (X_fitsne2,assignment)
   .NdOverlay.II :NdOverlay   [assignment]
      :Scatter   [X_fitsne1]   (X_fitsne2,leiden_labels)

In [22]:
scc.umap(adata)

UMAP(a=None, angular_rp_forest=False, b=None, init='spectral',
     learning_rate=1.0, local_connectivity=1.0, metric='euclidean',
     metric_kwds=None, min_dist=0.5, n_components=2, n_epochs=None,
     n_neighbors=15, negative_sample_rate=5, random_state=0,
     repulsion_strength=1.0, set_op_mix_ratio=1.0, spread=1.0,
     target_metric='categorical', target_metric_kwds=None,
     target_n_neighbors=-1, target_weight=0.5, transform_queue_size=4.0,
     transform_seed=42, verbose=True)
Construct fuzzy simplicial set
Fri Aug 23 12:01:41 2019 Finding Nearest Neighbors
Fri Aug 23 12:01:42 2019 Finished Nearest Neighbor Search
Fri Aug 23 12:01:43 2019 Construct embedding


//anaconda3/envs/sccloud/lib/python3.7/site-packages/umap/spectral.py:229: UserWarning: Embedding a total of 2 separate connected components using meta-embedding (experimental)
  n_components


	completed  0  /  500 epochs
	completed  50  /  500 epochs
	completed  100  /  500 epochs
	completed  150  /  500 epochs
	completed  200  /  500 epochs
	completed  250  /  500 epochs
	completed  300  /  500 epochs
	completed  350  /  500 epochs
	completed  400  /  500 epochs
	completed  450  /  500 epochs
Fri Aug 23 12:01:49 2019 Finished embedding
2019-08-23 12:01:49,159 - sccloud - INFO - using umap kNN graph 3219
2019-08-23 12:01:49,160 - sccloud - INFO - UMAP is calculated. Time spent = 7.34s.


In [23]:
scc.embedding(adata, basis = 'umap', keys = ['leiden_labels', 'assignment'])

:Layout
   .NdOverlay.I  :NdOverlay   [leiden_labels]
      :Scatter   [X_umap1]   (X_umap2,assignment)
   .NdOverlay.II :NdOverlay   [assignment]
      :Scatter   [X_umap1]   (X_umap2,leiden_labels)

In [24]:
scc.diffmap(adata)
scc.fle(adata, file_name = 'exp_out')

2019-08-23 12:01:50,165 - sccloud - INFO - Calculating connected components is done.
2019-08-23 12:01:50,182 - sccloud - INFO - Calculating normalized affinity matrix is done.
2019-08-23 12:01:50,539 - sccloud - INFO - diffmap finished. Time spent = 0.38s.
2019-08-23 12:01:50,967 - sccloud - INFO - Nearest neighbor search is finished in 0.43s.
2019-08-23 12:01:51,041 - sccloud - INFO - Constructing affinity matrix is done. Time spent = 0.07s.
2019-08-23 12:01:51,041 - sccloud - INFO - Affinity matrix calculation is finished in 0.07s
2019-08-23 12:01:51,108 - sccloud - INFO - Graph is constructed. Time spent = 0.07s.
exp_out.net is written.
['java', '-Djava.awt.headless=true', '-Xmx8g', '-cp', '//anaconda3/envs/sccloud/lib/python3.7/site-packages/forceatlas2/ext/forceatlas2.jar://anaconda3/envs/sccloud/lib/python3.7/site-packages/forceatlas2/ext/gephi-toolkit-0.9.2-all.jar', 'kco.forceatlas2.Main', '--input', 'exp_out.net', '--output', 'exp_out.coords', '--nthreads', '16', '--seed', '0'

In [25]:
scc.embedding(adata, basis = 'fle', keys = ['leiden_labels', 'assignment'])

:Layout
   .NdOverlay.I  :NdOverlay   [leiden_labels]
      :Scatter   [X_fle1]   (X_fle2,assignment)
   .NdOverlay.II :NdOverlay   [assignment]
      :Scatter   [X_fle1]   (X_fle2,leiden_labels)

## Differential Expression Analysis

In [26]:
scc.de_analysis(adata, cluster = 'leiden_labels', fisher = True, mwu = True)

2019-08-23 12:02:08,868 - sccloud - INFO - Collecting basic statistics is done. Time spent = 11.68s.
2019-08-23 12:02:09,072 - sccloud - INFO - Converting X to csc_matrix is done. Time spent = 0.20s.
2019-08-23 12:02:36,226 - sccloud - INFO - AUROC values are calculated. Time spent = 27.15s.
2019-08-23 12:02:36,945 - sccloud - INFO - Welch's t-test is done. Time spent = 0.72s.
2019-08-23 12:02:37,883 - sccloud - INFO - Fisher's exact test is done. Time spent = 0.94s.
2019-08-23 12:02:56,690 - sccloud - INFO - Mann-Whitney U test is done. Time spent = 18.81s.
2019-08-23 12:02:56,973 - sccloud - INFO - Differential expression analysis is finished. Time spent = 59.81s.


In [27]:
adata.varm

AxisArrays with keys: de_res

## Find Markers Using Deep Learning

In [28]:
markers = scc.find_markers(adata, label_attr = 'leiden_labels')

[1]	valid_0's multi_error: 0.0938902	valid_1's multi_error: 0.236025
Training until validation scores don't improve for 1 rounds.
[2]	valid_0's multi_error: 0.0552295	valid_1's multi_error: 0.18323
[3]	valid_0's multi_error: 0.0434933	valid_1's multi_error: 0.15528
[4]	valid_0's multi_error: 0.0303763	valid_1's multi_error: 0.136646
[5]	valid_0's multi_error: 0.0276148	valid_1's multi_error: 0.124224
[6]	valid_0's multi_error: 0.0210563	valid_1's multi_error: 0.130435
Early stopping, best iteration is:
[5]	valid_0's multi_error: 0.0276148	valid_1's multi_error: 0.124224
2019-08-23 12:03:20,226 - sccloud - INFO - LightGBM used 23.09s to train.
2019-08-23 12:03:26,272 - sccloud - INFO - find_markers took 29.24s to finish.


In [29]:
len(markers)

13

## Annotating Clusters

In [30]:
scc.infer_cell_types(adata, markers = 'mouse_brain', de_test = 't')

Cluster 1:
    name: Glutamatergic neuron; score: 0.50; average marker percentage: 68.26%; strong support: (Rbfox3+,95.33%),(Slc17a7+,41.18%)
Cluster 2:
Cluster 3:
    name: Glutamatergic neuron; score: 0.50; average marker percentage: 63.53%; strong support: (Rbfox3+,87.54%),(Slc17a7+,39.51%)
        name: Glutamatergic layer 6a; score: 1.00; average marker percentage: 69.00%; strong support: (Foxp2+,75.08%),(Tle4+,62.92%)
        name: Glutamatergic layer 6b; score: 0.50; average marker percentage: 62.92%; strong support: (Tle4+,62.92%)
Cluster 4:
    name: Glutamatergic neuron; score: 0.50; average marker percentage: 69.66%; strong support: (Rbfox3+,92.57%),(Slc17a7+,46.75%)
        name: Glutamatergic layer 5; score: 1.00; average marker percentage: 28.79%; strong support: (Deptor+,28.79%)
Cluster 5:
    name: GABAergic neuron; score: 0.75; average marker percentage: 41.67%; strong support: (Reln+,38.96%),(Gad1+,38.64%),(Gad2+,47.40%)
        name: GABAergic Sst interneuron; score: